In [44]:
import requests
from collections import defaultdict
import pandas as pd
from datetime import datetime
import matplotlib.pyplot as plt
from string import Template
from typing import List, Dict, Tuple, Union, Optional, Any
import numpy as np
from enum import Enum
import time
from tqdm import tqdm

pd.set_option("display.precision", 2)
pd.set_option('display.max_columns', None)

In [45]:
QUERY_BATCH_SIZE = 1000
HEADERS = {
    "Accept": "application/json, multipart/mixed",
    "Content-Type": "application/json",
}
DEFAULT_FROM_DATE = "1970-01-01T00:00:00"
DEFAULT_TO_DATE = "2038-01-19T03:14:07"
INVALID_ANSWER_HEX = "0xffffffffffffffffffffffffffffffffffffffffffffffffffffffffffffffff"
DECIMALS = 18


In [46]:
def str_to_timestamp(date_str):
    # Return the timestamp as a string
    return str(int(datetime.strptime(date_str, "%Y-%m-%dT%H:%M:%S").timestamp()))

def _to_content(q: str) -> dict[str, Any]:
    """Convert the given query string to payload content, i.e., add it under a `queries` key and convert it to bytes."""
    finalized_query = {
        "query": q,
        "variables": None,
        "extensions": {"headers": None},
    }
    return finalized_query

def wei_to_units(wei: int) -> float:
    return wei / 10**18

# calculate collateral amount
def calculate_collateral_amount(trade):
    """Calculate the collateral amount."""
    return int(trade["collateralVolume"]) / 10 ** DECIMALS

# calculate outcome token amount
def convert_hex_to_int(x: Union[str, float]) -> Union[int, float]:
    """Convert hex to int"""
    if isinstance(x, float):
        return np.nan
    elif isinstance(x, str):
        if x == INVALID_ANSWER_HEX:
            return -1
        else:
            return int(x, 16)
        
class MarketState(Enum):
    """Market state"""

    OPEN = 1
    PENDING = 2
    FINALIZING = 3
    ARBITRATING = 4
    CLOSED = 5

    def __str__(self) -> str:
        """Prints the market status."""
        return self.name.capitalize()

def determine_market_status(current_answer, opening_timestamp, is_pending_arbitration, answer_finalized_timestamp):
    """Determine the market status of a trade."""
    if current_answer is np.nan and time.time() >= opening_timestamp:
        return MarketState.PENDING
    elif current_answer == np.nan:
        return MarketState.OPEN
    elif answer_finalized_timestamp is None:
        return MarketState.PENDING
    elif is_pending_arbitration:
        return MarketState.ARBITRATING
    elif time.time() < answer_finalized_timestamp:
        return MarketState.FINALIZING
    return MarketState.CLOSED

In [47]:
fpmm_query_template = Template("""
{
  fixedProductMarketMakers(
    where: {
      creationTimestamp_gte: "$fpmm_creationTimestamp_gte",
      creationTimestamp_lt: "$fpmm_creationTimestamp_lte",
      id_gt: "$fpmm_id_gt",
      creator: "0x89c5cc945dd550bcffb72fe42bff002429f46fec"
    }
    first: ${first}
    orderBy: id
    orderDirection: asc
  ) {
    id
    creator
    creationTimestamp
    collateralToken
    conditions {
      id
      oracle
      questionId
      outcomeSlotCount
      payouts
    }
    fee
    collateralVolume
    outcomeTokenAmounts
    outcomeTokenMarginalPrices
    outcomeSlotCount
    liquidityMeasure
    liquidityParameter
    lastActiveDay
    runningDailyVolume
    lastActiveDayAndRunningDailyVolume
    scaledCollateralVolume
    scaledLiquidityMeasure
    scaledLiquidityParameter
    scaledRunningDailyVolume
    lastActiveDayAndScaledRunningDailyVolume
    curatedByDxDao
    condition
    question
    templateId
    data
    title
    outcomes
    category
    language
    arbitrator
    openingTimestamp
    timeout
    indexedOnQuestion
    resolutionTimestamp
    payouts
    currentAnswer
    currentAnswerBond
    currentAnswerTimestamp
    isPendingArbitration
    arbitrationOccurred
    answerFinalizedTimestamp
  }
}
""")

def _query_market_crator_data() -> List[Dict[str, Any]]:
    id_gt = ""
    all_trades = []
    first = QUERY_BATCH_SIZE

    while True:
        url = "https://api.thegraph.com/subgraphs/name/protofire/omen-xdai"

        content_json = _to_content(fpmm_query_template.substitute(
            fpmm_creationTimestamp_gte=str_to_timestamp(DEFAULT_FROM_DATE),
            fpmm_creationTimestamp_lte=str_to_timestamp(DEFAULT_TO_DATE),
            fpmm_id_gt=id_gt,
            first=first,
        ))
        headers = {
            "Accept": "application/json, multipart/mixed",
            "Content-Type": "application/json",
        }

        res = requests.post(url, headers=headers, json=content_json)

        if res.status_code == 200:
            trades_json = res.json()
            print(trades_json)
            all_trades.extend(trades_json['data']['fixedProductMarketMakers'])

            # new id_gt
            id_gt = trades_json['data']['fixedProductMarketMakers'][-1]['id']
            print(f'Fetched {len(trades_json["data"]["fixedProductMarketMakers"])} trades. New id_gt: {id_gt}')

            # if we fetched less than the batch size, we're done
            if len(trades_json['data']['fixedProductMarketMakers']) < QUERY_BATCH_SIZE:
                break
            
        else:
            print(f'Error fetching trades: {res.status_code}')
            break

    return all_trades

In [48]:
omen_xdai_trades_query = Template(
    """
    {
        fpmmTrades(
            where: {
                type: Buy,
                creationTimestamp_gte: "$fpmm_creationTimestamp_gte",
                creationTimestamp_lt: "$fpmm_creationTimestamp_lte",
                id_gt: "$id_gt",
            }
            first: $first
            orderBy: id
            orderDirection: asc
        ) {
            id
            title
            collateralToken
            outcomeTokenMarginalPrice
            oldOutcomeTokenMarginalPrice
            type
            creator {
                id
            }
            creationTimestamp
            collateralAmount
            collateralAmountUSD
            feeAmount
            outcomeIndex
            outcomeTokensTraded
            transactionHash
            fpmm {
                id
                outcomes
                title
                answerFinalizedTimestamp
                currentAnswer
                isPendingArbitration
                arbitrationOccurred
                openingTimestamp
                condition {
                    id
                }
            }
        }
    }
    """
)

def _query_omen_xdai_subgraph() -> dict[str, Any]:
    """Query the subgraph."""
    url = "https://api.thegraph.com/subgraphs/name/protofire/omen-xdai"

    grouped_results = defaultdict(list)
    id_gt = ""

    while True:
        query = omen_xdai_trades_query.substitute(
            # title=title,
            first=QUERY_BATCH_SIZE,
            id_gt=id_gt,
            fpmm_creationTimestamp_gte=str_to_timestamp(DEFAULT_FROM_DATE),
            fpmm_creationTimestamp_lte=str_to_timestamp(DEFAULT_TO_DATE),
        )
        content_json = _to_content(query)
        res = requests.post(url, headers=HEADERS, json=content_json)
        result_json = res.json()
        user_trades = result_json.get("data", {}).get("fpmmTrades", [])

        if not user_trades:
            break

        for trade in user_trades:
            fpmm_id = trade.get("fpmm", {}).get("id")
            grouped_results[fpmm_id].append(trade)

        id_gt = user_trades[len(user_trades) - 1]["id"]

    all_results = {
        "data": {
            "fpmmTrades": [
                trade
                for trades_list in grouped_results.values()
                for trade in trades_list
            ]
        }
    }

    return all_results

In [49]:
all_markets = _query_market_crator_data()
len(all_markets)

{'data': {'fixedProductMarketMakers': [{'id': '0x0094fa304017d5c2b355790e2976f769ea600492', 'creator': '0x89c5cc945dd550bcffb72fe42bff002429f46fec', 'creationTimestamp': '1692381990', 'collateralToken': '0xe91d153e0b41518a2ce8dd3d7944fa863463a97d', 'conditions': [{'id': '0xfa4b67aaf8f92ad6efbce485e8c34aedabdea66fc8cb675f045009b11c095927', 'oracle': '0xab16d643ba051c11962da645f74632d3130c81e2', 'questionId': '0x8d2a557c1469c27e80a196ac7bee90fc3ce2970f47b1ae370bce871574c2bd14', 'outcomeSlotCount': 2, 'payouts': None}], 'fee': '20000000000000000', 'collateralVolume': '176400000000000000', 'outcomeTokenAmounts': ['0', '0'], 'outcomeTokenMarginalPrices': None, 'outcomeSlotCount': 2, 'liquidityMeasure': '0', 'liquidityParameter': '0', 'lastActiveDay': '19591', 'runningDailyVolume': '117600000000000000', 'lastActiveDayAndRunningDailyVolume': '2268482820248261584543179167305204802753412269584564290097013528416626122775986176', 'scaledCollateralVolume': '0.1764', 'scaledLiquidityMeasure': '0', 

2052

In [50]:
all_trades = _query_omen_xdai_subgraph()

In [51]:
class PredictionMarket:
    def __init__(self):
        self.liquidity = {'Yes': 0, 'No': 0}
        self.fees = 0
        self.traded_tokens = {'Yes': 0, 'No': 0}
        self.token_price = None
        
    def create_tokens(self, initial_value):
        A = 10 
        B = 100 / A

        token_value = initial_value / (A + B)
        return A, B, token_value
    
    def deposit(self, dai):
        # Equal distribution of Yes and No tokens
        Yes, No, token_price = self.create_tokens(dai)
        self.liquidity['Yes'] += Yes
        self.liquidity['No'] += No
        self.token_price = token_price
        return self.token_price
    
    def buy_tokens(self, dai, token_type):
        fee = dai * 0.02
        self.fees += fee
        dai -= fee

        # new tokens created
        new_tokens = dai / self.token_price

        # create new yes/no tokens
        self.liquidity[token_type] += new_tokens
        self.liquidity['No' if token_type == 'Yes' else 'Yes'] += new_tokens

        if token_type == 'Yes':
            current_yes = self.liquidity['Yes']
            current_no = self.liquidity['No']

            # Calculate new amount of No tokens to maintain constant product
            new_yes = 100 / current_no

            # Update liquidity
            self.liquidity['Yes'] = new_yes

            # Update traded tokens
            self.traded_tokens['Yes'] += current_yes - new_yes
            return current_yes - new_yes
        
        elif token_type == 'No':
            current_yes = self.liquidity['Yes']
            current_no = self.liquidity['No']

            # Calculate new amount of Yes tokens to maintain constant product
            new_no = 100 / current_yes

            # Update liquidity
            self.liquidity['No'] = new_no

            # Update traded tokens
            self.traded_tokens['No'] += current_no - new_no
            return current_no - new_no
        
    def withdraw(self):
        # Calculate DAI and tokens to withdraw
        higher_token = 'Yes' if self.liquidity['Yes'] > self.liquidity['No'] else 'No'
        lower_token = 'Yes' if higher_token == 'No' else 'No'

        # calculate DAI to withdraw
        dai_withdrawn = self.liquidity[lower_token]

        # calculate remaining yes/no tokens
        remaining_tokens = self.liquidity[higher_token] - self.liquidity[lower_token]

        # convert remaining tokens to DAI
        remaining_tokens = remaining_tokens * self.token_price

        return {
            'dai': dai_withdrawn,
            'tokens': {
                higher_token: remaining_tokens,
                lower_token: 0
            },
            'fees': self.fees
        }

In [52]:
STATS_DF_COLUMNS = [
    "id",
    "creator",
    "creationTimestamp",
    "collateralToken",
    "investment",
    "num_trades",
    "market_status",
    "current_answer",
    "answer_finalized_timestamp",
    "trade_fees",
    "withdraw",
    "net_earnings", # withdraw + trade_fees - investment
]
    

In [53]:
def conversion_ratio(token_a, token_b):
    """Conversion ratio between two tokens"""
    return token_a / (token_a + token_b)


def analyse(market, all_trades):
    # initialize stats dataframe
    stats_df = pd.DataFrame(columns=STATS_DF_COLUMNS)

    # liquidity pool tracking
    liquidity = PredictionMarket()

    # only consider binary markets
    if market['outcomeSlotCount'] != 2:
        print(f"Outcome slot count is not 2: {market['outcomeSlotCount']}")
        return
    
    # market opening timestamp
    if isinstance(market["openingTimestamp"], str):
        opening_timestamp = int(market["openingTimestamp"])
    else:
        print(f"Opening timestamp is not a string: {market['openingTimestamp']}")
        return

    # market is pending arbitration
    is_pending_arbitration = market["isPendingArbitration"]

    # market answer finalized timestamp
    if isinstance(market["answerFinalizedTimestamp"], str):
        answer_finalized_timestamp = int(market["answerFinalizedTimestamp"])
    else:
        answer_finalized_timestamp = None
    
    # market status
    ms = determine_market_status(
        market["currentAnswer"], 
        opening_timestamp, 
        is_pending_arbitration, 
        answer_finalized_timestamp
    )

    # only consider closed markets
    if ms != MarketState.CLOSED:
        print(f"Market is not closed: {ms}")
        return

    # market creator data
    investment = calculate_collateral_amount(market)
    trade_fees = float(market['scaledCollateralVolume']) * 0.02 # 2% trade fees
    liquidity.deposit(investment)

    # get all trades for this market
    trades = [trade for trade in all_trades if trade['fpmm']['id'] == market['id']]
    num_trades = len(trades)

    if len(trades) == 0:
        # todo: double check this
        profit_loss = 0
        stats_df.loc[0] = [
            market['id'],
            market['creator'],
            market['creationTimestamp'],
            market['collateralToken'],
            investment,
            num_trades,
            ms,
            market['currentAnswer'],
            answer_finalized_timestamp,
            trade_fees,
            liquidity.withdraw(),
            profit_loss
        ]
        return stats_df
    
    # Process trades
    for trade in trades:
        trade_outcome_index = int(trade['outcomeIndex'])
        trade_collateral_amount = wei_to_units(int(trade['collateralAmount']))
        if trade_outcome_index == 0:
            liquidity.buy_tokens(trade_collateral_amount, 'Yes')
            
        elif trade_outcome_index == 1:
            liquidity.buy_tokens(trade_collateral_amount, 'No')

    # Calculate the final token value
    withdraw = liquidity.withdraw()

    # correct answer
    market_outcome_index = convert_hex_to_int(market["currentAnswer"])
    if market_outcome_index == -1:
        profit_loss = withdraw['dai'] + trade_fees - investment
    else:
        market_resolved_to_yes = True if market_outcome_index == 0 else False
        token_value_yes = 1 if market_resolved_to_yes else 0
        token_value_no = 1 if not market_resolved_to_yes else 0

        # Calculate the final token value
        final_value = withdraw['tokens']['Yes'] * token_value_yes + withdraw['tokens']['No'] * token_value_no
        profit_loss = final_value + trade_fees - investment

    # add stats to dataframe dont use append
    stats_df.loc[0] = [
        market['id'],
        market['creator'],
        market['creationTimestamp'],
        market['collateralToken'],
        investment,
        num_trades,
        ms,
        market['currentAnswer'],
        answer_finalized_timestamp,
        trade_fees,
        withdraw,
        profit_loss
    ]
    return stats_df

In [57]:
df = pd.DataFrame(columns=STATS_DF_COLUMNS)
for market in tqdm(all_markets):
    if df is None:
        df = analyse(market, all_trades['data']['fpmmTrades'])
    else:
        df = pd.concat([df, analyse(market, all_trades['data']['fpmmTrades'])])

  0%|          | 9/2052 [00:00<00:49, 41.58it/s]

Market is not closed: Finalizing


  3%|▎         | 62/2052 [00:01<00:36, 54.52it/s]

Market is not closed: Pending


  4%|▎         | 74/2052 [00:01<00:36, 53.77it/s]

...

Market is not closed: Pending


 99%|█████████▉| 2033/2052 [01:09<00:00, 23.19it/s]

Market is not closed: Pending


100%|██████████| 2052/2052 [01:10<00:00, 29.17it/s]

Market is not closed: Finalizing


In [62]:
df.sort_values(by='investment', ascending=False)

id  \
0   0x4ddd1c0239c536f7fc1b73d8bf7de6788895cee0   
0   0x5ef227808e00982e1bf0ed75f204455e9d302d0f   
0   0xab0e3cd20ae065f1c6e5731b549866104c6e5db6   
0   0xc60de79e00fa741a42ae1c54e907514ac977fbeb   
0   0x6c026ab0464f520b20d81cec69ba03fc1fa60699   
..                                         ...   
0   0xca0ad658a68a260863ef6d51bd7a2c26581f7871   
0   0xbf84f51df51532a0c51417805c5f7d004cad73ae   
0   0x23f971af39b764d148b269777fcd62e510c73564   
0   0xc8274e0626aca2619050b956e48be12c08ea52cc   
0   0xd0ad031793d3f95bf0b7cb58ba40cd02afb809ac   

                                       creator creationTimestamp  \
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1693915145   
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1692804105   
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1692382575   
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1692893400   
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1702640915   
..                                         ...               ...   
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1699007410   
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1699569585   
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1689871770   
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1699569350   
0   0x89c5cc945dd550bcffb72fe42bff002429f46fec        1699569475   

                               collateralToken  investment num_trades  \
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d       29.08         21   
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d       22.96         13   
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d       21.84          5   
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d       19.82         11   
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d       19.40         28   
..                                         ...         ...        ...   
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d        0.00          0   
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d        0.00          0   
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d        0.00          0   
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d        0.00          0   
0   0xe91d153e0b41518a2ce8dd3d7944fa863463a97d        0.00          0   

   market_status                                     current_answer  \
0         Closed  0x00000000000000000000000000000000000000000000...   
0         Closed  0x00000000000000000000000000000000000000000000...   
0         Closed  0x00000000000000000000000000000000000000000000...   
0         Closed  0xffffffffffffffffffffffffffffffffffffffffffff...   
0         Closed  0x00000000000000000000000000000000000000000000...   
..           ...                                                ...   
0         Closed  0x00000000000000000000000000000000000000000000...   
0         Closed  0x00000000000000000000000000000000000000000000...   
0         Closed  0x00000000000000000000000000000000000000000000...   
0         Closed  0x00000000000000000000000000000000000000000000...   
0         Closed  0x00000000000000000000000000000000000000000000...   

   answer_finalized_timestamp  trade_fees  \
0                  1694315875        0.58   
0                  1693181185        0.46   
0                  1692924520        0.44   
0                  1693382385        0.40   
0                  1703155950        0.39   
..                        ...         ...   
0                  1699457515        0.00   
0                  1699975640        0.00   
0                  1696279250        0.00   
0                  1699976735        0.00   
0                  1699976150        0.00   

                                             withdraw  net_earnings  
0   {'dai': 3.630272196670972, 'tokens': {'Yes': 3...        -28.50  
0   {'dai': 3.3333333333333335, 'tokens': {'Yes': ...        -22.50  
0   {'dai': 3.6676336952903967, 'tokens': {'Yes': ...        -21.40  
0   {'dai': 5.032959390967412, 'tokens': {'Yes': 1...        -14.39  
0   {

In [63]:
df['investment'].sum()

5215.859237373838